In [ ]:
%%capture
import os
os.environ["UNSLOTH_VLLM_STANDBY"] = "1" # [NEW] Extra 30% context lengths!
if "COLAB_" not in "".join(os.environ.keys()):
    # If you're not in Colab, just use pip install or uv pip install
    !pip install unsloth vllm
else:
    pass # For Colab / Kaggle, we need extra instructions hidden below \/

In [2]:
!pip install unsloth vllm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.5/61.5 kB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 347.3/347.3 kB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 438.2/438.2 MB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 180.0/180.0 kB 17.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 111.0/111.0 kB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.4/45.4 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 133.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 118.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.2/117.2 MB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.7/8.7 MB 141.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.1/60.1 MB 12.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 506.

In [ ]:
#@title Colab Extra Install { display-mode: "form" }
%%capture
import os
!pip install --upgrade -qqq uv
if "COLAB_" not in "".join(os.environ.keys()):
    # If you're not in Colab, just use pip install!
    !pip install unsloth vllm
else:
    try: import numpy; get_numpy = f"numpy=={numpy.__version__}"
    except: get_numpy = "numpy"
    try: import subprocess; is_t4 = "Tesla T4" in str(subprocess.check_output(["nvidia-smi"]))
    except: is_t4 = False
    get_vllm, get_triton = ("vllm==0.9.2", "triton==3.2.0") if is_t4 else ("vllm==0.10.2", "triton")
    !uv pip install -qqq --upgrade \
        unsloth {get_vllm} {get_numpy} torchvision bitsandbytes xformers
    !uv pip install -qqq {get_triton}
!uv pip install transformers==4.55.4
!uv pip install --no-deps trl==0.22.2

In [1]:
from unsloth import FastModel
from datasets import load_dataset
import torch, re, random
from transformers import AutoTokenizer, AutoModelForCausalLM

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


INFO 10-29 18:05:23 [__init__.py:216] Automatically detected platform cuda.
ERROR 10-29 18:05:24 [fa_utils.py:57] Cannot use FA version 2 is not supported due to FA2 is only supported on devices with compute capability >= 8
🦥 Unsloth Zoo will now patch everything to make training faster!


In [2]:
# Load the Gemma-3 1B Instruct model using FastModel (Unsloth integration for faster loading)
model, tokenizer = FastModel.from_pretrained(
    model_name = "unsloth/gemma-3-1b-it",   # Instruction-tuned Gemma-3 model (1B parameters)

    # max_seq_length = max_seq_length,      # Optional: set if you need longer input contexts (e.g., 8k–32k tokens)

    load_in_4bit = False,                   # Use 4-bit quantization to drastically reduce GPU memory (set True if limited VRAM)
    load_in_8bit = False,                   # Use 8-bit quantization (more accurate than 4-bit, but uses roughly 2× memory)

    full_finetuning = False,                # Set True only if you plan to fine-tune all model parameters
                                            # Here we keep False since we’re evaluating, not training

    # token = "hf_...",                     # Optional: required if the model is gated or private on Hugging Face Hub
)

==((====))==  Unsloth 2025.10.11: Fast Gemma3 patching. Transformers: 4.57.1. vLLM: 0.11.0.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.8.0+cu126. CUDA: 7.5. CUDA Toolkit: 12.6. Triton: 3.4.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.32.post1. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: Using float16 precision for gemma3 won't work! Using float32.
Unsloth: Gemma3 does not support SDPA - switching to fast eager.
Unsloth: QLoRA and full finetuning all not selected. Switching to 16bit LoRA.


model.safetensors:   0%|          | 0.00/2.00G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/233 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/4.69M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/33.4M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/35.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/670 [00:00<?, ?B/s]

chat_template.jinja: 0.00B [00:00, ?B/s]

In [16]:
model = FastModel.get_peft_model(
    model,
    finetune_vision_layers     = False, # Turn off for just text!
    finetune_language_layers   = True,  # Should leave on!
    finetune_attention_modules = True,  # Attention good for GRPO
    finetune_mlp_modules       = True,  # SHould leave on always!

    r = 8,           # Larger = higher accuracy, but might overfit
    lora_alpha = 8,  # Recommended alpha == r at least
    lora_dropout = 0,
    bias = "none",
    random_state = 3407,
)

Unsloth: Making `model.base_model.model.model` require gradients


In [66]:
from datasets import load_dataset
ds = load_dataset("race", "all", split="train[:10000]")

In [67]:
ds[0]

{'example_id': 'high19088.txt',
 'article': 'Last week I talked with some of my students about what they wanted to do after they graduated, and what kind of job prospects  they thought they had.\nGiven that I teach students who are training to be doctors, I was surprised do find that most thought that they would not be able to get the jobs they wanted without "outside help". "What kind of help is that?" I asked, expecting them to tell me that they would need a   or family friend to help them out.\n"Surgery ," one replied.\nI was pretty alarmed by that response. It seems that the graduates of today are increasingly willing to go under the knife to get ahead of others when it comes to getting a job .\nOne girl told me that she was considering surgery to increase her height. "They break your legs, put in special extending screws, and slowly expand the gap between the two ends of the bone as it re-grows, you can get at least 5 cm taller!"\nAt that point, I was shocked. I am short, I can\'t

In [68]:
def build_prompt(article, question, options):
    LETTERS = "ABCD"
    opts = "\n".join(f"{l}) {o}" for l, o in zip(LETTERS[:len(options)], options))
    return (
        "Read the passage and reason step-by-step before answering.\n\n"
        f"Passage:\n{article}\n\n"
        f"Question: {question}\n\n"
        f"Options:\n{opts}\n\n"
        "Output EXACTLY two lines in this order:\n"
        "Reasoning: <your concise reasoning>\n"
        "Final: <LETTER>\n"
        "After the 'Final' line, output NOTHING else."
    )

# Match variants of: "Final: A" / "Final answer: b"
LETTER_RE = re.compile(r'(?i)\bfinal(?:\s*answer)?\s*:\s*([ABCD])\b')

In [97]:
import re, math
LETTER_RE = re.compile(r'final(?:\s*answer)?\s*:\s*([A-D])', re.IGNORECASE)

# weights you can tweak
CORRECT = 1.0
INCORRECT = -0.5     # penalize wrong letters
MALFORMED = -1.0      # stronger penalty for no 'Final: <LETTER>'

def mc_reward_grpo(completions, answer=None, **kwargs):
    penalty = float(kwargs.get("malformed_penalty", MALFORMED))

    if isinstance(completions, str):
        completions = [completions]

    texts = []
    for c in completions or []:
        if isinstance(c, list) and c and isinstance(c[-1], dict):
            texts.append(str(c[-1].get("content", "")))
        elif isinstance(c, dict):
            texts.append(str(c.get("content", "")))
        else:
            texts.append("" if c is None else str(c))

    n = len(texts)

    if answer is None:
        golds = [None] * n
    else:
        golds = [answer] if isinstance(answer, str) else list(answer)
        if len(golds) != n:
            golds = (golds * math.ceil(n / max(1, len(golds))))[:n]

    rewards = []
    for txt, g in zip(texts, golds):
        m = LETTER_RE.findall(txt or "")
        if not m:
            rewards.append(penalty)                 # malformed
            continue
        pred = m[-1].upper()
        if g is None:
            rewards.append(CORRECT)                 # well-formed bonus if no gold provided
        else:
            rewards.append(CORRECT if pred == str(g).upper() else INCORRECT)
    return rewards

In [100]:
def reward_validated(completions, **kwargs):
    r = mc_reward_grpo(completions, **kwargs)
    exp = len(completions) if not isinstance(completions, str) else 1
    if len(r) != exp:
        print(f"[WARN] rewards len {len(r)} != {exp}")
    else:
        # compact stats
        import numpy as np
        arr = np.array(r, dtype=float)
        print(f"[REWARD] n={len(r)} mean={arr.mean():.3f} std={arr.std(ddof=0):.3f} "
              f"min={arr.min():.3f} max={arr.max():.3f}")
    return r

In [71]:
# 1) Flat, single generation per prompt
prompts = ["p1", "p2", "p3"]
comps   = ["Final: A", "Final: B", "I think it's C"]
answers = ["A", "B", "C"]
print(mc_reward_grpo(comps, answers))
# -> [1.0, 1.0, 0.0]   (malformed third → 0.0)

# 2) Nested: 2 generations per prompt
prompts = ["p1", "p2"]
comps   = [
    ["Final: A", "Final: C"],      # for p1
    ["No final", "Final: B"]       # for p2
]
answers = ["A", "B"]
print(mc_reward_grpo(comps, answers))
# -> [1.0, 0.0, 0.0, 1.0]

# 3) Last 'Final:' wins
prompts = ["p1"]
comps   = [["Final: A, Final: C, Final: B"]]
answers = ["B"]
print(mc_reward_grpo(comps, answers))
# -> [1.0]

# 4) Penalize malformed stronger
print(mc_reward_grpo(["just text"], ["A"], malformed_penalty=-1.0))
# -> [-1.0]

# 5) TRL shape with dict/list-of-dicts
print(mc_reward_grpo([{"content": "Final: D"}], ["D"]))
# -> [1.0]
print(mc_reward_grpo([[{"content": "Final: C"}]], ["C"]))
# -> [1.0]

# 6) output string
print(mc_reward_grpo("Final: B", ["D"]))
# -> [1.0]
print(mc_reward_grpo([[{"content": "Final: C"}]], ["C"]))
# -> [1.0]

[1.0, 1.0, -0.5]
[-0.25, 1.0]
[1.0]
[-1.0]
[1.0]
[1.0]
[-0.25]
[1.0]


In [98]:
# Map dataset to expected columns
ds = ds.map(lambda x: {
    "prompt": build_prompt(x["article"], x["question"], x["options"]),
    "answer": x["answer"],   # keeps gold letter
})

Map:   0%|          | 0/10000 [00:00<?, ? examples/s]

In [73]:
ds[0]

{'example_id': 'high19088.txt',
 'article': 'Last week I talked with some of my students about what they wanted to do after they graduated, and what kind of job prospects  they thought they had.\nGiven that I teach students who are training to be doctors, I was surprised do find that most thought that they would not be able to get the jobs they wanted without "outside help". "What kind of help is that?" I asked, expecting them to tell me that they would need a   or family friend to help them out.\n"Surgery ," one replied.\nI was pretty alarmed by that response. It seems that the graduates of today are increasingly willing to go under the knife to get ahead of others when it comes to getting a job .\nOne girl told me that she was considering surgery to increase her height. "They break your legs, put in special extending screws, and slowly expand the gap between the two ends of the bone as it re-grows, you can get at least 5 cm taller!"\nAt that point, I was shocked. I am short, I can\'t

In [74]:
# ensure PAD is set
if tokenizer.pad_token_id is None:
    tokenizer.pad_token_id = tokenizer.eos_token_id
if getattr(model.config, "pad_token_id", None) is None:
    model.config.pad_token_id = tokenizer.pad_token_id

In [92]:
from transformers import StoppingCriteria, StoppingCriteriaList
import re
LETTER_LINE_RE = re.compile(r'(?mi)^\s*Final\s*:\s*([A-D])\s*$')
class FinalLetterStop(StoppingCriteria):
    def __init__(self, tok): self.tok = tok
    def __call__(self, input_ids, scores, **kw):
        txt = self.tok.decode(input_ids[0], skip_special_tokens=True)
        return bool(LETTER_LINE_RE.search(txt))

stopper = StoppingCriteriaList([FinalLetterStop(tokenizer)])

In [114]:
GEN_KW = dict(
    max_new_tokens=128,
    do_sample=True,
    eos_token_id=tokenizer.eos_token_id,
    pad_token_id=tokenizer.pad_token_id,
    top_p =  0.95,
    max_length = 1024,
    #stopping_criteria=stopper,
)

max_seq_length = 1024  # your prompt ca

In [106]:
i = 100
row = ds[i]
prompt, gold = row["prompt"], row["answer"]

enc = tokenizer(prompt, return_tensors="pt", truncation=True, max_length=1024).to(model.device)
with torch.no_grad():
    out_ids = model.generate(**enc, **GEN_KW)

gen_only = out_ids[:, enc["input_ids"].shape[1]:]
completion = tokenizer.decode(gen_only[0], skip_special_tokens=True)
print(completion)

print("Reward:", mc_reward_grpo(completion, answer=gold)[0])



Reasoning: The passage emphasizes that while studies have been made, there's still a need for more thorough investigation into the relationship between geography and climate and the impact on people’s health. The author suggests that generalizations are insufficient and that a deeper understanding of the complex factors involved is required.
Final: D

Reward: 1.0


In [119]:
from trl import GRPOConfig, GRPOTrainer

training_args = GRPOConfig(
    learning_rate=5e-6,
    adam_beta1=0.9,
    adam_beta2=0.99,
    weight_decay=0.1,
    warmup_ratio=0.1,
    lr_scheduler_type="cosine",
    optim="adamw_torch_fused",      # OK if CUDA + PyTorch supports fused; else use "adamw_torch"
    logging_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=1,
    num_generations=4,              # adjust for memory
    max_prompt_length=max_seq_length,
    max_completion_length=128,      # ← start modest; you can raise later
    #max_steps=50,
    num_train_epochs=1,
    save_steps=50,                  # or set > max_steps to skip checkpointing
    max_grad_norm=0.1,
    beta=0.02,                      # small KL helps keep format stable; set 0.0 if you prefer
    report_to="none",
    output_dir="outputs",
    generation_kwargs=GEN_KW,       # ← make GRPO use the same decoding you validated
    #max_length = max_seq_length,    # ← make GRPO use the same decoding you validated
    #generation_config = GEN_KW,     # ← make GRPO use the same decoding you validated
    seed=42,
)

Unsloth: We now expect `per_device_train_batch_size` to be a multiple of `num_generations`.
We will change the batch size of 1 to the `num_generations` of 4


In [120]:
trainer = GRPOTrainer(
    model=model,                # or pass model_id string
    processing_class=tokenizer,
    #reward_funcs=mc_reward_grpo,
    reward_funcs=reward_validated,
    args=training_args,
    train_dataset=ds,
)

The model is already on multiple devices. Skipping the move to device specified in `args`.


Unsloth: Switching to float32 training since model cannot work with float16


In [ ]:
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 10,000 | Num Epochs = 1 | Total steps = 10,000
O^O/ \_/ \    Batch size per device = 4 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (4 x 1 x 1) = 4
 "-____-"     Trainable parameters = 6,522,880 of 1,006,408,832 (0.65% trained)


[REWARD] n=4 mean=-0.750 std=0.250 min=-1.000 max=-0.500


[REWARD] n=4 mean=1.000 std=0.000 min=1.000 max=1.000
[REWARD] n=4 mean=-0.375 std=0.820 min=-1.000 max=1.000
[REWARD] n=4 mean=-0.625 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=0.500 std=0.866 min=-1.000 max=1.000
[REWARD] n=4 mean=-0.875 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=-0.875 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=-0.875 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=-0.500 std=0.866 min=-1.000 max=1.000
[REWARD] n=4 mean=0.250 std=0.750 min=-0.500 max=1.000
[REWARD] n=4 mean=-0.875 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=0.125 std=0.893 min=-1.000 max=1.000
[REWARD] n=4 mean=-0.750 std=0.250 min=-1.000 max=-0.500
[REWARD] n=4 mean=0.500 std=0.866 min=-1.000 max=1.000
[REWARD] n=4 mean=-1.000 std=0.000 min=-1.000 max=-1.000
[REWARD] n=4 mean=0.625 std=0.650 min=-0.500 max=1.000
[REWARD] n=4 mean=0.000 std=1.000 min=-1.000 max=1.000
[REWARD] n=4 mean=-0.250 std=0.750 min=-1.000 max=1.000
[REWARD] n=4 mean=-0.625 std=0.217 min=-1.000 max

[REWARD] n=4 mean=1.000 std=0.000 min=1.000 max=1.000
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=1.000 std=0.000 min=1.000 max=1.000
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=0.625 std=0.650 min=-0.500 max=1.000
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=-0.625 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=1.000 std=0.000 min=1.000 max=1.000
[REWARD] n=4 mean=1.000 std=0.000 min=1.000 max=1.000
[REWARD] n=4 mean=-0.625 std=0.217 min=-1.000 max=-0.500
[REWARD] n=4 mean=-0.125 std=0.650 min=-0.500 max=1.000
[REWARD] n=4 mean=0.250 std=0.750 min=-0.500 max=1.000
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=-0.500 std=0.000 min=-0.500 max=-0.500
[REWARD] n=4 mean=0.250 std=0.750 min=-0.500 max=1.000
[REWARD] n=4 mean=0.625 std=0.650 min=-0.500 max=1

In [83]:
len(ds)

10000

In [ ]:
from google.colab import userdata
hf_token = userdata.get('hf_wr')

In [ ]:
model.push_to_hub("jdmartinev/gemma-3-grpo", token = hf_token) # Online saving
tokenizer.push_to_hub("jdmartinev/gemma-3-grpo", token = hf_token) # Online saving

README.md:   0%|          | 0.00/577 [00:00<?, ?B/s]

Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...uo7ip2m/model.safetensors:   2%|1         | 38.1MB / 2.00GB            

Saved model to https://huggingface.co/jdmartinev/gemma-3-grpo


README.md:   0%|          | 0.00/584 [00:00<?, ?B/s]

Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...mps0qfrr7z/tokenizer.json:   1%|1         |  469kB / 33.4MB            

  ...ps0qfrr7z/tokenizer.model: 100%|##########| 4.69MB / 4.69MB            

In [ ]:
ds_test = load_dataset("race", "all", split="train[10000:20000]")

In [ ]:
import random
id = random.randint(0,10)
print(ds_test[id])
prompt = build_prompt(ds_test[id]["article"], ds_test[id]["question"], ds_test[id]["options"])
input_ids = tokenizer(prompt, return_tensors="pt").to(model.device)
with torch.no_grad():
  output_ids = model.generate(**input_ids)

out = tokenizer.decode(output_ids[0], skip_special_tokens=True)
reward = mc_reward(out, ds_test[id]["answer"])
print(f"Reward: {reward}")

{'example_id': 'high5984.txt', 'article': 'Although cats may be one of the most popular pets today, little is known about how and when humans and cats set up their close relationship.\nThe earliest evidence for human-cat interaction dates back to prehistoric Cyprus , where the remains of a wild cat and a human -- dated 9,500 years old -- were found buried together.\nA new study in the Proceedings of the National Academy of Sciences has confirmed the first direct evidence of a human-domestic cat relationship among Chinese farmers 5,300 years ago. Researchers studied the bones of cats, dogs, deer and other animals unearthed in an excavation   near a village in Central China. By using some ways, scientists showed that the cats were living on a mostly millet -based diet, just like the domesticated dogs and pigs from the site.\n"The most reasonable explanation for a high consumption of millet-based food is that the cats had formed a stable and mutual relationship with humans and could easil

In [ ]:
out

'Read the passage and reason step-by-step before answering.\n\nPassage:\nAlthough cats may be one of the most popular pets today, little is known about how and when humans and cats set up their close relationship.\nThe earliest evidence for human-cat interaction dates back to prehistoric Cyprus , where the remains of a wild cat and a human -- dated 9,500 years old -- were found buried together.\nA new study in the Proceedings of the National Academy of Sciences has confirmed the first direct evidence of a human-domestic cat relationship among Chinese farmers 5,300 years ago. Researchers studied the bones of cats, dogs, deer and other animals unearthed in an excavation   near a village in Central China. By using some ways, scientists showed that the cats were living on a mostly millet -based diet, just like the domesticated dogs and pigs from the site.\n"The most reasonable explanation for a high consumption of millet-based food is that the cats had formed a stable and mutual relationsh